In [1]:
from matplotlib import pyplot as plt
from tqdm import tqdm
import pandas as pd
import numpy as np
import pytesseract
import shutil
import cv2
import os

# psm 6 = Assume a single uniform block of text.
config_tesseract = '--tessdata-dir ./ttesseract_langs --psm 6'

In [2]:
def read_resize_data(input_file, size=160):
    img = cv2.imread(input_file)
    
    width = size
    height = size
    dim = (width, height)

    # resize image
    resized = cv2.resize(img, dim, interpolation = cv2.INTER_AREA)

    return resized


In [3]:
def read_input_file_list():
    # input_data = pd.read_csv(r'labelled_images_just_sipa2.txt', names=["file_name","seen_value","ncol2","ncol3"], sep="\t", header=None)
    input_data = pd.read_csv(r'./labelled_images_sipa3.txt', names=["file_name","seen_value","ncol2","ncol3"], sep="\t", header=None)
    input_data = input_data.reset_index()

    print(len(input_data), "input images")
    return input_data

In [4]:
def get_text(image):

    # Read text from image using Seven Segment training data
    text_ssd = pytesseract.image_to_string(image, lang="ssd", config=config_tesseract)

    # Read text from image using English character training data
    text_eng = pytesseract.image_to_string(image, lang="eng", config=config_tesseract)
    
    # Clean text
    text_ssd = ''.join(c for c in text_ssd if c.isdigit() or c == '.')
    text_eng = ''.join(c for c in text_eng if c.isdigit() or c == '.')

    return text_ssd, text_eng


In [5]:
def process_file_closing(input_file, size):

    # Get image data
    # img = read_input_data(input_file)
    img = read_resize_data(input_file, size)

    # Convert to RGB (three dimensions)
    nimRGB = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)

    # Convert to gray (one dimension)
    nimGray = cv2.cvtColor(nimRGB, cv2.COLOR_BGR2GRAY)

    # Perform Dilation using a 5x5 matrix
    cdilation = cv2.dilate(nimGray, np.ones((5,5), np.uint8))

    # PErform Erod using a 5x5 matrix
    nimClosing = cv2.erode(cdilation, np.ones((5,5), np.uint8))

    # Get Text for Seven Segment and English
    text_ssd, text_eng = get_text(nimClosing)
    
    return text_ssd, text_eng
    

In [6]:
def mask_red(img):

    # img=cv2.imread('./sipaimages/2/22319_20220321100409.jpg')
    img_hsv=cv2.cvtColor(img, cv2.COLOR_BGR2HSV)

    # lower mask (0-10)
    lower_red = np.array([0,50,50])
    upper_red = np.array([40,255,255])
    mask0 = cv2.inRange(img_hsv, lower_red, upper_red)

    # upper mask (170-180)
    lower_red = np.array([170,50,50])
    upper_red = np.array([180,255,255])
    mask1 = cv2.inRange(img_hsv, lower_red, upper_red)

    # join my masks
    mask = mask0+mask1

    # set my output img to zero everywhere except my mask
    output_img = img.copy()
    output_img[np.where(mask==0)] = 0

    return output_img


In [7]:
def process_mask_otsu(input_file, size):

    # Get image data
    # img = read_input_data(input_file)
    img = read_resize_data(input_file, size)

    imgMask = mask_red(img)
    
    # Convert to RGB (three dimensions)
    nimRGB = cv2.cvtColor(imgMask, cv2.COLOR_BGR2RGB)

    # Convert to gray (one dimension)
    nimGray = cv2.cvtColor(nimRGB, cv2.COLOR_BGR2GRAY)

    # 0 means threshold level which actually is omitted because we used CV_THRESH_OTSU flag
    min_threshold = 0

    # 255 is a value that is going to be assigned to respectively pixels in the result 
    # (namely, to all pixels which value in the source is greater then computed threshold level)
    max_threshold = 255

    # THRESH_BINARY | THRESH_OTSU is a required flag to perform Otsu thresholding. Because in fact we would like to perform binary thresholding,
    # so we use CV_THRESH_BINARY (you can use any of 5 flags opencv provides) combined with CV_THRESH_OTSU
    value, nimOTSU = cv2.threshold(nimGray, min_threshold, max_threshold, cv2.THRESH_BINARY | cv2.THRESH_OTSU)

    # Get Text for Seven Segment and English
    text_ssd, text_eng = get_text(nimOTSU)
    
    return text_ssd, text_eng

In [8]:
def control_loop(loop_counter):
    input_array = []
    print(loop_counter)

    for row in tqdm(input_data.iterrows()):

        input_file = row[1][1]
        seen_value = row[1][2]
        # print("input_file", input_file)

        size = loop_counter
        # Dialation
        closing_ssd, closing_eng = process_file_closing(input_file, size)

        # Mask Red OTSU
        mro_ssd, mro_eng = process_mask_otsu(input_file, size)

        # Add text to array
        new_row = [input_file, seen_value, loop_counter, closing_ssd, closing_eng, mro_ssd, mro_eng]

        input_array.append(new_row)

    return input_array





In [ ]:
input_data = read_input_file_list()
input_array = []
size_array = []

for loop_counter in range(190,250):
    # print(loop_counter)
    # vv = control_loop(loop_counter)
    loop_array = control_loop(loop_counter)
    # loop_array = [loop_counter]
    size_array.append(loop_array)

size_array

In [10]:
len(size_array)

60

In [12]:
sa = np.array(size_array)

In [13]:
sa.tofile("size_Array.csv", sep=",", format='%s')

In [ ]:
adf = pd.DataFrame(sa)

In [15]:
sa.shape

(50, 26, 7)

In [15]:
size_array[1]

[['.\\sipaimages\\3\\1.jpg', 30.31, 191, '031', '031', '', ''],
 ['.\\sipaimages\\3\\10.jpg', 13.05, 191, '136', '1305', '4111111', '4'],
 ['.\\sipaimages\\3\\11.jpg', 20.59, 191, '5', '5', '', ''],
 ['.\\sipaimages\\3\\12.jpg', 13.05, 191, '1109', '1305', '', ''],
 ['.\\sipaimages\\3\\13.jpg', 30.31, 191, '0.3', '303', '', ''],
 ['.\\sipaimages\\3\\14.jpg', 13.04, 191, '1504', '1304', '4.11', ''],
 ['.\\sipaimages\\3\\15.jpg', 30.24, 191, '0', '30', '14', '4'],
 ['.\\sipaimages\\3\\16.jpg', 13.04, 191, '1804', '1304', '', ''],
 ['.\\sipaimages\\3\\17.jpg', 13.03, 191, '13.9', '1303', '144', '1543'],
 ['.\\sipaimages\\3\\18.jpg', 30.23, 191, '40.2', '30.23', '11.1', '02'],
 ['.\\sipaimages\\3\\19.jpg', 3.76, 191, '3.10', '316', '76', '76'],
 ['.\\sipaimages\\3\\2.jpg', 30.31, 191, '01', '031', '', ''],
 ['.\\sipaimages\\3\\20.jpg', 30.23, 191, '0411', '02', '111', ''],
 ['.\\sipaimages\\3\\21.jpg', 33.99, 191, '39.91', '390', '', ''],
 ['.\\sipaimages\\3\\22.jpg', 3.75, 191, '1', '3', 

In [16]:
for row in tqdm(input_data.iterrows()):
    input_file = row[1][1]
    print("input_file", input_file)
    seen_value = row[1][2]
    print(seen_value)


26it [00:00, 17287.87it/s]

input_file .\sipaimages\3\1.jpg
30.31
input_file .\sipaimages\3\10.jpg
13.05
input_file .\sipaimages\3\11.jpg
20.59
input_file .\sipaimages\3\12.jpg
13.05
input_file .\sipaimages\3\13.jpg
30.31
input_file .\sipaimages\3\14.jpg
13.04
input_file .\sipaimages\3\15.jpg
30.24
input_file .\sipaimages\3\16.jpg
13.04
input_file .\sipaimages\3\17.jpg
13.03
input_file .\sipaimages\3\18.jpg
30.23
input_file .\sipaimages\3\19.jpg
3.76
input_file .\sipaimages\3\2.jpg
30.31
input_file .\sipaimages\3\20.jpg
30.23
input_file .\sipaimages\3\21.jpg
33.99
input_file .\sipaimages\3\22.jpg
3.75
input_file .\sipaimages\3\23.jpg
30.23
input_file .\sipaimages\3\24.jpg
30.24
input_file .\sipaimages\3\25.jpg
33.99
input_file .\sipaimages\3\26.jpg
3.75
input_file .\sipaimages\3\3.jpg
13.04
input_file .\sipaimages\3\4.jpg
13.05
input_file .\sipaimages\3\5.jpg
30.3
input_file .\sipaimages\3\6.jpg
13.04
input_file .\sipaimages\3\7.jpg
13.04
input_file .\sipaimages\3\8.jpg
30.31
input_file .\sipaimages\3\9.jpg
13.04

In [17]:
ad1 = np.genfromtxt("size_Array.csv", delimiter=",")

In [18]:
ad1.shape

(10920,)

In [19]:
len(ad1)

10920

In [33]:
for x in ad1:
    print(x)

nan
5679.0
100.0
44.0
nan
5679.0
1.0
nan
2244.0
100.0
nan
nan
2244.0
2244.0
nan
2244.0
100.0
4.0
nan
2244.0
nan
nan
2244.0
100.0
nan
nan
2244.0
2.0
nan
7244.0
100.0
4.0
nan
7244.0
24.0
nan
7244.0
100.0
nan
nan
7244.0
nan
nan
1234.0
100.0
nan
nan
1.0
nan
nan
1234.0
100.0
100.0
nan
11.0
nan
nan
6543.0
100.0
nan
nan
78.0
nan
nan
1234.0
100.0
11.0
nan
234.0
3.0
nan
1234.0
100.0
1234.0
3.0
11.0
734.0
nan
1234.0
100.0
190.0
nan
nan
nan
nan
1234.0
100.0
nan
nan
11824.0
0.0
nan
1234.0
100.0
nan
nan
11234.0
nan
nan
1234.0
100.0
nan
nan
nan
nan
nan
4321.0
100.0
19.0
nan
4231.0
nan
nan
4321.0
100.0
nan
nan
422117.0
3.0
nan
4321.0
100.0
nan
nan
4221.0
nan
nan
4321.0
100.0
nan
nan
6311.0
4324.0
nan
672.0
100.0
88.0
nan
672.0
62.0
nan
674.0
100.0
nan
nan
674.0
nan
nan
675.0
100.0
nan
nan
351.0
675.0
nan
678.0
100.0
nan
nan
678.0
578.0
nan
678.0
100.0
nan
nan
678.0
8.0
nan
678.0
100.0
nan
nan
137151.0
5718.0
nan
678.0
100.0
nan
nan
678.0
678.0
nan
678.0
100.0
nan
nan
678.0
578.0
nan
678.0
100.0
nan
n

In [37]:
import json
import csv

In [39]:
data = size_array


In [40]:
with open('tmp_file.txt', 'w') as f:
    csv.writer(f, delimiter=' ').writerows(data)